Nama : Cintha Hafrida Putri
ID Dicoding : cintha_bang


# Proyek Pengembangan Machine Learning Pipeline

# Import Library

Mengunduh dan menginstal TFX versi 1.15.1 beserta semua dependensinya, sehingga dapat mulai menggunakannya dalam proyek pengembangan machine learning pipeline ini.

In [1]:
pip install tfx==1.15.1

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 60.4/60.4 kB 1.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.7/89.7 kB 5.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 152.0/152.0 kB 9.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 43.5/43.5 kB 2.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 173.5/173.5 kB 10.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.9/99.9 kB 6.8 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 51.8/51.8 kB 3.6 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.0/3.0 MB 47.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.8/1.8 MB 60.3 MB/s eta 0:

In [2]:
import os
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import tensorflow as tf
import nltk
import string
import tensorflow_data_validation as tfdv

from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import word_tokenize,sent_tokenize
from nltk.tokenize.toktok import ToktokTokenizer
from nltk.stem import LancasterStemmer,WordNetLemmatizer
from nltk import pos_tag
from nltk.corpus import wordnet
from string import punctuation

from tfx.components import CsvExampleGen, StatisticsGen, SchemaGen, ExampleValidator, Transform, Trainer, Tuner
from tfx.proto import example_gen_pb2
from tfx.orchestration.experimental.interactive.interactive_context import InteractiveContext

nltk.download('stopwords')
nltk.download('averaged_perceptron_tagger')
nltk.download('wordnet')
nltk.download('punkt')

[nltk_data] Downloading package stopwords to /root/nltk_data...
[nltk_data]   Unzipping corpora/stopwords.zip.
[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Unzipping taggers/averaged_perceptron_tagger.zip.
[nltk_data] Downloading package wordnet to /root/nltk_data...
[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.


True

# Directory Pipeline


Dalam kode ini, saya mendefinisikan beberapa variabel kunci untuk pipeline machine learning saya, termasuk PIPELINE_NAME yang menyimpan nama pipeline ("cintha_bang-pipeline"), PIPELINE_ROOT yang merupakan direktori utama untuk pipeline, SCHEMA_PIPELINE_NAME untuk nama skema validasi data ("fake-news-tfdv-schema"), METADATA_PATH yang menyimpan lokasi file metadata untuk pipeline di database SQLite, dan SERVING_MODEL_DIR yang menunjukkan direktori tempat model yang telah dilatih akan disajikan. Kode ini membantu dalam pengelolaan dan strukturisasi berbagai komponen pipeline dengan lebih baik.

In [3]:
PIPELINE_NAME = "cintha_bang-pipeline"
PIPELINE_ROOT = os.path.join('pipelines', PIPELINE_NAME)
SCHEMA_PIPELINE_NAME = "fake-news-tfdv-schema"
METADATA_PATH = os.path.join('metadata', PIPELINE_NAME, 'metadata.db')
SERVING_MODEL_DIR = os.path.join('serving_model_dir', PIPELINE_NAME)

# Data Understanding

Pada tahap ini dilakukan untuk memahami dataset sebelum analisis.

## Data Loading

data_dir untuk menyimpan direktori sumber data mentah ('data'), data_clean untuk menyimpan direktori tempat data yang telah dibersihkan ('data_clean'), dan file_name untuk menyimpan nama file data mentah yang akan diproses ('fake_job_postings.csv'). Variabel-variabel ini membantu dalam pengorganisasian struktur penyimpanan data agar lebih mudah diakses selama proses pengolahan.

In [4]:
data_dir = 'data'
data_clean = 'data_clean'
file_name = 'fake_job_postings.csv'

Tahap ini adalah memuat dataset. Saya menggunakan google drive agar lebih mudah.

**Dataset :** Real/Fake Job Posting Prediction dari Kaggle https://www.kaggle.com/datasets/shivamb/real-or-fake-fake-jobposting-prediction

In [5]:
df=pd.read_csv('/content/drive/MyDrive/DICODING MACHINE LEARNING/Machine Learning Operations (MLOps)/fake_job_postings.csv')
df.head()

job_id                                      title            location  \
0       1                           Marketing Intern    US, NY, New York   
1       2  Customer Service - Cloud Video Production      NZ, , Auckland   
2       3    Commissioning Machinery Assistant (CMA)       US, IA, Wever   
3       4          Account Executive - Washington DC  US, DC, Washington   
4       5                        Bill Review Manager  US, FL, Fort Worth   

  department salary_range                                    company_profile  \
0  Marketing          NaN  We're Food52, and we've created a groundbreaki...   
1    Success          NaN  90 Seconds, the worlds Cloud Video Production ...   
2        NaN          NaN  Valor Services provides Workforce Solutions th...   
3      Sales          NaN  Our passion for improving quality of life thro...   
4        NaN          NaN  SpotSource Solutions LLC is a Global Human Cap...   

                                         description  \
0  Food52, a fast-growing, James Beard Award-winn...   
1  Organised - Focused - Vibrant - Awesome!Do you...   
2  Our client, located in Houston, is actively se...   
3  THE COMPANY: ESRI – Environmental Systems Rese...   
4  JOB TITLE: Itemization Review ManagerLOCATION:...   

                                        requirements  \
0  Experience with content management systems a m...   
1  What we expect from you:Your key responsibilit...   
2  Implement pre-commissioning and commissioning ...   
3  EDUCATION: Bachelor’s or Master’s in GIS, busi...   
4  QUALIFICATIONS:RN license in the State of Texa...   

                                            benefits  telecommuting  \
0                                                NaN              0   
1  What you will get from usThrough being part of...              0   
2                                                NaN              0   
3  Our culture is anything but corporate—we have ...              0   
4                              Full Benefits Offered              0   

   has_company_logo  has_questions employment_type required_experience  \
0                 1              0           Other          Internship   
1                 1              0       Full-time      Not Applicable   
2                 1              0             NaN                 NaN   
3                 1              0       Full-time    Mid-Senior level   
4                 1              1       Full-time    Mid-Senior level   

  required_education                   industry              function  \
0                NaN                        NaN             Marketing   
1                NaN  Marketing and Advertising      Customer Service   
2                NaN                        NaN                   NaN   
3  Bachelor's Degree          Computer Software                 Sales   
4  Bachelor's Degree     Hospital & Health Care  Health Care Provider   

   fraudulent  
0           0  
1           0  
2           0  
3           0  
4           0

# EDA

In [6]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17880 entries, 0 to 17879
Data columns (total 18 columns):
 #   Column               Non-Null Count  Dtype 
---  ------               --------------  ----- 
 0   job_id               17880 non-null  int64 
 1   title                17880 non-null  object
 2   location             17534 non-null  object
 3   department           6333 non-null   object
 4   salary_range         2868 non-null   object
 5   company_profile      14572 non-null  object
 6   description          17879 non-null  object
 7   requirements         15185 non-null  object
 8   benefits             10670 non-null  object
 9   telecommuting        17880 non-null  int64 
 10  has_company_logo     17880 non-null  int64 
 11  has_questions        17880 non-null  int64 
 12  employment_type      14409 non-null  object
 13  required_experience  10830 non-null  object
 14  required_education   9775 non-null   object
 15  industry             12977 non-null  object
 16  func

In [7]:
df.shape

(17880, 18)

In [8]:
df.describe()

job_id  telecommuting  has_company_logo  has_questions  \
count  17880.000000   17880.000000      17880.000000   17880.000000   
mean    8940.500000       0.042897          0.795302       0.491723   
std     5161.655742       0.202631          0.403492       0.499945   
min        1.000000       0.000000          0.000000       0.000000   
25%     4470.750000       0.000000          1.000000       0.000000   
50%     8940.500000       0.000000          1.000000       0.000000   
75%    13410.250000       0.000000          1.000000       1.000000   
max    17880.000000       1.000000          1.000000       1.000000   

         fraudulent  
count  17880.000000  
mean       0.048434  
std        0.214688  
min        0.000000  
25%        0.000000  
50%        0.000000  
75%        0.000000  
max        1.000000

In [9]:
df.isna().sum()

job_id                     0
title                      0
location                 346
department             11547
salary_range           15012
company_profile         3308
description                1
requirements            2695
benefits                7210
telecommuting              0
has_company_logo           0
has_questions              0
employment_type         3471
required_experience     7050
required_education      8105
industry                4903
function                6455
fraudulent                 0
dtype: int64

Karena kita akan menggabungkan kolom menjadi text maka missing value akan diubah menjadi spasi

## Data Preparation

In [10]:
df.fillna(" ",inplace = True)

Menghapus kolom yang tidak diperlukan

In [11]:
df = df.drop(columns=['job_id', 'telecommuting', 'has_questions', 'has_company_logo', 'salary_range'])

In [12]:
df.head()

title            location department  \
0                           Marketing Intern    US, NY, New York  Marketing   
1  Customer Service - Cloud Video Production      NZ, , Auckland    Success   
2    Commissioning Machinery Assistant (CMA)       US, IA, Wever              
3          Account Executive - Washington DC  US, DC, Washington      Sales   
4                        Bill Review Manager  US, FL, Fort Worth              

                                     company_profile  \
0  We're Food52, and we've created a groundbreaki...   
1  90 Seconds, the worlds Cloud Video Production ...   
2  Valor Services provides Workforce Solutions th...   
3  Our passion for improving quality of life thro...   
4  SpotSource Solutions LLC is a Global Human Cap...   

                                         description  \
0  Food52, a fast-growing, James Beard Award-winn...   
1  Organised - Focused - Vibrant - Awesome!Do you...   
2  Our client, located in Houston, is actively se...   
3  THE COMPANY: ESRI – Environmental Systems Rese...   
4  JOB TITLE: Itemization Review ManagerLOCATION:...   

                                        requirements  \
0  Experience with content management systems a m...   
1  What we expect from you:Your key responsibilit...   
2  Implement pre-commissioning and commissioning ...   
3  EDUCATION: Bachelor’s or Master’s in GIS, busi...   
4  QUALIFICATIONS:RN license in the State of Texa...   

                                            benefits employment_type  \
0                                                              Other   
1  What you will get from usThrough being part of...       Full-time   
2                                                                      
3  Our culture is anything but corporate—we have ...       Full-time   
4                              Full Benefits Offered       Full-time   

  required_experience required_education                   industry  \
0          Internship                                                 
1      Not Applicable                     Marketing and Advertising   
2                                                                     
3    Mid-Senior level  Bachelor's Degree          Computer Software   
4    Mid-Senior level  Bachelor's Degree     Hospital & Health Care   

               function  fraudulent  
0             Marketing           0  
1      Customer Service           0  
2                                 0  
3                 Sales           0  
4  Health Care Provider           0

Membuat kolom yang berisikan text dimana text berasal dari semua kolom dataset yang disatukan

In [13]:
df['text'] = df['title'] + ' ' + df['location'] + ' ' + df['department'] + ' ' + df['company_profile'] + ' ' + df['description'] + ' ' + df['requirements'] + ' ' + df['benefits'] + ' ' + df['employment_type'] + ' ' + df['required_education'] + ' ' + df['industry'] + ' ' + df['function']

Cek apakah kolom text sudah masuk

In [14]:
df.head()

title            location department  \
0                           Marketing Intern    US, NY, New York  Marketing   
1  Customer Service - Cloud Video Production      NZ, , Auckland    Success   
2    Commissioning Machinery Assistant (CMA)       US, IA, Wever              
3          Account Executive - Washington DC  US, DC, Washington      Sales   
4                        Bill Review Manager  US, FL, Fort Worth              

                                     company_profile  \
0  We're Food52, and we've created a groundbreaki...   
1  90 Seconds, the worlds Cloud Video Production ...   
2  Valor Services provides Workforce Solutions th...   
3  Our passion for improving quality of life thro...   
4  SpotSource Solutions LLC is a Global Human Cap...   

                                         description  \
0  Food52, a fast-growing, James Beard Award-winn...   
1  Organised - Focused - Vibrant - Awesome!Do you...   
2  Our client, located in Houston, is actively se...   
3  THE COMPANY: ESRI – Environmental Systems Rese...   
4  JOB TITLE: Itemization Review ManagerLOCATION:...   

                                        requirements  \
0  Experience with content management systems a m...   
1  What we expect from you:Your key responsibilit...   
2  Implement pre-commissioning and commissioning ...   
3  EDUCATION: Bachelor’s or Master’s in GIS, busi...   
4  QUALIFICATIONS:RN license in the State of Texa...   

                                            benefits employment_type  \
0                                                              Other   
1  What you will get from usThrough being part of...       Full-time   
2                                                                      
3  Our culture is anything but corporate—we have ...       Full-time   
4                              Full Benefits Offered       Full-time   

  required_experience required_education                   industry  \
0          Internship                                                 
1      Not Applicable                     Marketing and Advertising   
2                                                                     
3    Mid-Senior level  Bachelor's Degree          Computer Software   
4    Mid-Senior level  Bachelor's Degree     Hospital & Health Care   

               function  fraudulent  \
0             Marketing           0   
1      Customer Service           0   
2                                 0   
3                 Sales           0   
4  Health Care Provider           0   

                                                text  
0  Marketing Intern US, NY, New York Marketing We...  
1  Customer Service - Cloud Video Production NZ, ...  
2  Commissioning Machinery Assistant (CMA) US, IA...  
3  Account Executive - Washington DC US, DC, Wash...  
4  Bill Review Manager US, FL, Fort Worth   SpotS...

Setelah membuat kolom text maka langkah selanjutnya adalah menghapus kolom lainnya karena tidak diperlukan

In [15]:
df = df.drop(columns=['title', 'location', 'department', 'company_profile', 'description', 'requirements', 'benefits', 'employment_type', 'required_experience', 'required_education', 'industry', 'function'])

In [16]:
df.head()

fraudulent                                               text
0           0  Marketing Intern US, NY, New York Marketing We...
1           0  Customer Service - Cloud Video Production NZ, ...
2           0  Commissioning Machinery Assistant (CMA) US, IA...
3           0  Account Executive - Washington DC US, DC, Wash...
4           0  Bill Review Manager US, FL, Fort Worth   SpotS...

In [17]:
df['tokens'] = df['text'].apply(word_tokenize)

In [18]:
# Inisialisasi daftar stopwords dalam bahasa Inggris
stop = set(stopwords.words('english'))

# Menghapus stopwords
df['tokens'] = df['tokens'].apply(lambda x: [word for word in x if word.lower() not in stop])

In [19]:
# Menggabungkan kembali token menjadi satu string dan menyimpan sebagai clean_text
df['clean_text'] = df['tokens'].apply(lambda x: ' '.join(x))

Langkah selanjutnya adalah mengonversi tag part-of-speech (POS) yang diperoleh dari pemrosesan teks menggunakan pustaka Natural Language Toolkit (nltk) ke dalam bentuk yang lebih sederhana, yaitu kategori POS yang dapat digunakan oleh WordNet.

In [20]:
def get_simple_pos(tag):
    if tag.startswith('J'):
        return wordnet.ADJ
    elif tag.startswith('V'):
        return wordnet.VERB
    elif tag.startswith('N'):
        return wordnet.NOUN
    elif tag.startswith('R'):
        return wordnet.ADV
    else:
        return wordnet.NOUN

Melakukan proses lemmatization pada teks input dengan menghilangkan stopwords dan mengonversi kata-kata menjadi bentuk dasar atau lemma-nya.

In [21]:
lemmatizer = WordNetLemmatizer()

def lemmatize_words(text):
    final_text = []
    for i in text.split():
        if i.strip().lower() not in stop:
            pos = pos_tag([i.strip()])
            word = lemmatizer.lemmatize(i.strip(),get_simple_pos(pos[0][1]))
            final_text.append(word.lower())
    return " ".join(final_text)

In [22]:
df.clean_text = df.clean_text.apply(lemmatize_words)

In [23]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 17880 entries, 0 to 17879
Data columns (total 4 columns):
 #   Column      Non-Null Count  Dtype 
---  ------      --------------  ----- 
 0   fraudulent  17880 non-null  int64 
 1   text        17880 non-null  object
 2   tokens      17880 non-null  object
 3   clean_text  17880 non-null  object
dtypes: int64(1), object(3)
memory usage: 558.9+ KB


Hapus kolom yang sudah tidak diperlukan

In [24]:
df = df.drop(columns=['tokens', 'text'])

In [25]:
df.head()

fraudulent                                         clean_text
0           0  marketing intern us , ny , new york marketing ...
1           0  customer service - cloud video production nz ,...
2           0  commissioning machinery assistant ( cma ) us ,...
3           0  account executive - washington dc us , dc , wa...
4           0  bill review manager us , fl , fort worth spots...

In [26]:
if not os.path.exists(data_clean):
    os.makedirs(data_clean)

In [27]:
df.to_csv(os.path.join(data_clean, "fake_job_postings_clean.csv"), index=False)

In [28]:
interactive_context = InteractiveContext(pipeline_root=PIPELINE_ROOT)

# Load Datset menggunakan Example Gen

Mengonfigurasi dan menginisialisasi komponen ExampleGen, yang bertanggung jawab untuk menghasilkan contoh data dari file CSV dan membagi data tersebut ke dalam beberapa set (split) untuk keperluan pelatihan dan evaluasi model.

In [29]:
output = example_gen_pb2.Output(
    split_config=example_gen_pb2.SplitConfig(splits=[
        example_gen_pb2.SplitConfig.Split(name="train", hash_buckets=8),
        example_gen_pb2.SplitConfig.Split(name="test", hash_buckets=2),
    ])
)

example_gen = CsvExampleGen(input_base=data_clean, output_config=output)

In [30]:
interactive_context.run(example_gen)

ExecutionResult(
    component_id: CsvExampleGen
    execution_id: 1
    outputs:
        examples: OutputChannel(artifact_type=Examples, producer_component_id=CsvExampleGen, output_key=examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

## Summary Statistic

Menjalankan komponen StatisticsGen untuk menghasilkan statistik dari data contoh (examples) yang dihasilkan oleh example_gen, dalam konteks interaktif.

In [31]:
statistics_gen = StatisticsGen(
    examples=example_gen.outputs["examples"]
)
interactive_context.run(statistics_gen)

ExecutionResult(
    component_id: StatisticsGen
    execution_id: 2
    outputs:
        statistics: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=StatisticsGen, output_key=statistics, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Menampilkan statistik data yang dihasilkan oleh komponen StatisticsGen secara interaktif, sehingga Anda bisa melihat distribusi dan ringkasan data yang telah diproses.

In [36]:
interactive_context.show(statistics_gen.outputs["statistics"])

# Data Schema

Membuat komponen SchemaGen yang secara otomatis menghasilkan skema (schema) data berdasarkan statistik yang dihasilkan oleh StatisticsGen.

In [37]:
schema_gen = SchemaGen(
    statistics=statistics_gen.outputs["statistics"],
)
interactive_context.run(schema_gen)

ExecutionResult(
    component_id: SchemaGen
    execution_id: 3
    outputs:
        schema: OutputChannel(artifact_type=Schema, producer_component_id=SchemaGen, output_key=schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [38]:
interactive_context.show(schema_gen.outputs["schema"])

Type  Presence Valency Domain
Feature name                                
'clean_text'  BYTES  required              -
'fraudulent'    INT  required              -

# Membuat Validator

Menjalankan komponen ExampleValidator, yang memvalidasi data input berdasarkan statistik dari StatisticsGen dan skema dari SchemaGen. Komponen ini mendeteksi anomali atau data yang tidak sesuai dengan skema, seperti tipe data yang salah atau nilai yang melampaui batas, sehingga memastikan kualitas dan konsistensi data dalam pipeline machine learning.

In [39]:
example_validator = ExampleValidator(
    statistics=statistics_gen.outputs["statistics"],
    schema=schema_gen.outputs["schema"],
)
interactive_context.run(example_validator)

ExecutionResult(
    component_id: ExampleValidator
    execution_id: 4
    outputs:
        anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=ExampleValidator, output_key=anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [40]:
interactive_context.show(example_validator.outputs["anomalies"])

# Preprocessing Data

In [41]:
TRANSFORM_MODULE_FILE = "transform.py"

In [45]:
%%writefile {TRANSFORM_MODULE_FILE}
import tensorflow as tf

LABEL_KEY = "fraudulent"
FEATURE_KEY = "clean_text"

def transformed_name(key):
    return f"{key}_xf"

def preprocessing_fn(inputs):

    outputs = {}

    outputs[transformed_name(FEATURE_KEY)] = tf.strings.lower(inputs[FEATURE_KEY])

    outputs[transformed_name(LABEL_KEY)] = tf.cast(inputs[LABEL_KEY], tf.int64)

    return outputs

Overwriting transform.py


"overwriting transform.py" menunjukkan bahwa file tuner.py yang sudah ada sebelumnya sedang ditimpa dengan konten baru karena saya merevisi kode sehingga menjalankannya 2 kali

In [46]:
transform = Transform(
    examples=example_gen.outputs["examples"],
    schema=schema_gen.outputs["schema"],
    module_file=os.path.abspath(TRANSFORM_MODULE_FILE)
)

In [47]:
interactive_context.run(transform)

ExecutionResult(
    component_id: Transform
    execution_id: 6
    outputs:
        transform_graph: OutputChannel(artifact_type=TransformGraph, producer_component_id=Transform, output_key=transform_graph, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        transformed_examples: OutputChannel(artifact_type=Examples, producer_component_id=Transform, output_key=transformed_examples, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        updated_analyzer_cache: OutputChannel(artifact_type=TransformCache, producer_component_id=Transform, output_key=updated_analyzer_cache, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=pre_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        pre_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=pre_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_schema: OutputChannel(artifact_type=Schema, producer_component_id=Transform, output_key=post_transform_schema, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_stats: OutputChannel(artifact_type=ExampleStatistics, producer_component_id=Transform, output_key=post_transform_stats, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        post_transform_anomalies: OutputChannel(artifact_type=ExampleAnomalies, producer_component_id=Transform, output_key=post_transform_anomalies, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

# Tuner Hyperparameter

In [48]:
TUNER_MODULE_FILE = "tuner.py"

In [49]:
%%writefile {TUNER_MODULE_FILE}

from typing import NamedTuple, Dict, Text, Any
import keras_tuner as kt
import tensorflow as tf
import tensorflow_transform as tft
from keras_tuner.engine import base_tuner
from keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs

LABEL_KEY = "fraudulent"
FEATURE_KEY = "clean_text"
NUM_EPOCHS = 5

TunerFnResult = NamedTuple("TunerFnResult", [
    ("tuner", base_tuner.BaseTuner),
    ("fit_kwargs", Dict[Text, Any]),
])

early_stopping_callback = tf.keras.callbacks.EarlyStopping(
    monitor="val_binary_accuracy",
    mode="max",
    verbose=1,
    patience=10,
)

def transformed_name(key):
    return f"{key}_xf"

def gzip_reader_fn(filenames):
    return tf.data.TFRecordDataset(filenames, compression_type="GZIP")

def input_fn(file_pattern, tf_transform_output, num_epochs, batch_size=64):
    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy()
    )

    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY),
    )

    return dataset

def model_builder(hp, vectorizer_layer):
    num_hidden_layers = hp.Choice(
        "num_hidden_layers", values=[1, 2]
    )
    embed_dims = hp.Int(
        "embed_dims", min_value=16, max_value=128, step=32
    )
    lstm_units = hp.Int(
        "lstm_units", min_value=32, max_value=128, step=32
    )
    dense_units = hp.Int(
        "dense_units", min_value=32, max_value=256, step=32
    )
    dropout_rate = hp.Float(
        "dropout_rate", min_value=0.1, max_value=0.5, step=0.1
    )
    learning_rate = hp.Choice(
        "learning_rate", values=[1e-2, 1e-3, 1e-4]
    )

    inputs = tf.keras.Input(
        shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string
    )

    x = vectorizer_layer(inputs)
    x = layers.Embedding(input_dim=5000, output_dim=embed_dims)(x)
    x = layers.Bidirectional(layers.LSTM(lstm_units))(x)

    for _ in range(num_hidden_layers):
        x = layers.Dense(dense_units, activation=tf.nn.relu)(x)
        x = layers.Dropout(dropout_rate)(x)

    outputs = layers.Dense(1, activation=tf.nn.sigmoid)(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        optimizer=tf.keras.optimizers.Adam(learning_rate=learning_rate),
        loss=tf.keras.losses.BinaryCrossentropy(from_logits=True),
        metrics=["binary_accuracy"],
    )

    return model


def tuner_fn(fn_args: FnArgs):
    tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    train_set = input_fn(
        fn_args.train_files[0], tf_transform_output, NUM_EPOCHS
    )

    eval_set = input_fn(
        fn_args.eval_files[0], tf_transform_output, NUM_EPOCHS
    )

    vectorizer_dataset = train_set.map(
        lambda f, l: f[transformed_name(FEATURE_KEY)]
    )

    vectorizer_layer = layers.TextVectorization(
        max_tokens=5000,
        output_mode="int",
        output_sequence_length=500,
    )
    vectorizer_layer.adapt(vectorizer_dataset)

    tuner = kt.RandomSearch(
         hypermodel=lambda hp: model_builder(hp, vectorizer_layer),
         objective=kt.Objective('binary_accuracy', direction='max'),
         max_trials = 5,
         directory=fn_args.working_dir,
         project_name="kt_RandomSearch",
     )

    return TunerFnResult(
        tuner=tuner,
        fit_kwargs={
            "callbacks": [early_stopping_callback],
            "x": train_set,
            "validation_data": eval_set,
            "steps_per_epoch": fn_args.train_steps,
            "validation_steps": fn_args.eval_steps,
        },
    )

Writing tuner.py


 "writing tuner.py" menunjukkan bahwa kode Anda sedang disimpan ke dalam file yang bernama tuner.py

Mengkonfigurasi dan menginisialisasi komponen Tuner dalam arsitektur TFX (TensorFlow Extended)

In [52]:
from tfx.components import Tuner
from tfx.proto import trainer_pb2

tuner = Tuner(
    module_file=os.path.abspath(TUNER_MODULE_FILE),
    examples=transform.outputs["transformed_examples"],
    transform_graph=transform.outputs["transform_graph"],
    schema=schema_gen.outputs["schema"],
    train_args=trainer_pb2.TrainArgs(splits=["train"], num_steps=20),
    eval_args=trainer_pb2.EvalArgs(splits=["test"], num_steps=5),
)

In [53]:
interactive_context.run(tuner)

Trial 5 Complete [00h 01m 28s]
binary_accuracy: 0.9320312738418579

Best binary_accuracy So Far: 0.957812488079071
Total elapsed time: 00h 04m 54s
Results summary
Results in pipelines/cintha_bang-pipeline/.temp/8/kt_RandomSearch
Showing 10 best trials
Objective(name="binary_accuracy", direction="max")

Trial 3 summary
Hyperparameters:
num_hidden_layers: 1
embed_dims: 112
lstm_units: 32
dense_units: 192
dropout_rate: 0.2
learning_rate: 0.01
Score: 0.957812488079071

Trial 1 summary
Hyperparameters:
num_hidden_layers: 2
embed_dims: 48
lstm_units: 96
dense_units: 192
dropout_rate: 0.4
learning_rate: 0.0001
Score: 0.944531261920929

Trial 4 summary
Hyperparameters:
num_hidden_layers: 2
embed_dims: 80
lstm_units: 128
dense_units: 96
dropout_rate: 0.2
learning_rate: 0.001
Score: 0.9320312738418579

Trial 2 summary
Hyperparameters:
num_hidden_layers: 2
embed_dims: 48
lstm_units: 128
dense_units: 128
dropout_rate: 0.30000000000000004
learning_rate: 0.01
Score: 0.921093761920929

Trial 0 summar

ExecutionResult(
    component_id: Tuner
    execution_id: 8
    outputs:
        best_hyperparameters: OutputChannel(artifact_type=HyperParameters, producer_component_id=Tuner, output_key=best_hyperparameters, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        tuner_results: OutputChannel(artifact_type=TunerResults, producer_component_id=Tuner, output_key=tuner_results, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

Output dari pencarian hyperparameter menggunakan TFX Tuner menunjukkan bahwa percobaan ke-5 mencapai akurasi 93,2%, sementara akurasi terbaik sepanjang pencarian adalah 95,8% dari percobaan ke-3. Total waktu pencarian adalah 4 menit dan 54 detik, dengan ringkasan hasil disimpan di direktori yang ditentukan. Berikut adalah ringkasan dari percobaan terbaik:

Trial 3: Akurasi tertinggi 95,8%, hyperparameter: 1 hidden layer, 112 embedding dimensions, 32 LSTM units, 192 dense units, 0,2 dropout rate, dan learning rate 0,01.

- Trial 1: Akurasi 94,5%.
- Trial 4: Akurasi 93,2%.
- Trial 2: Akurasi 92,1%.
- Trial 0: Akurasi 91%.

# Training Model

In [54]:
TRAINER_MODULE_FILE = "trainer.py"

In [55]:
%%writefile {TRAINER_MODULE_FILE}

import os
import tensorflow as tf
import tensorflow_transform as tft
from keras import layers
from tfx.components.trainer.fn_args_utils import FnArgs

LABEL_KEY = "fraudulent"
FEATURE_KEY = "clean_text"
NUM_EPOCHS = 3

early_stopping_callback = tf.keras.callbacks.EarlyStopping(
    monitor="val_binary_accuracy",
    mode="max",
    verbose=1,
    patience=10,
)

def transformed_name(key):
    return key + "_xf"


def gzip_reader_fn(filenames):
    return tf.data.TFRecordDataset(filenames, compression_type='GZIP')


def input_fn(file_pattern,
             tf_transform_output,
             num_epochs,
             batch_size=64) -> tf.data.Dataset:

    transform_feature_spec = (
        tf_transform_output.transformed_feature_spec().copy())

    dataset = tf.data.experimental.make_batched_features_dataset(
        file_pattern=file_pattern,
        batch_size=batch_size,
        features=transform_feature_spec,
        reader=gzip_reader_fn,
        num_epochs=num_epochs,
        label_key=transformed_name(LABEL_KEY))

    return dataset

def model_builder(vectorizer_layer, hyperparameters):
    inputs = tf.keras.Input(
        shape=(1,), name=transformed_name(FEATURE_KEY), dtype=tf.string
    )

    x = vectorizer_layer(inputs)
    x = layers.Embedding(
        input_dim=5000,
        output_dim=hyperparameters["embed_dims"])(x)
    x = layers.Bidirectional(layers.LSTM(hyperparameters["lstm_units"]))(x)

    for _ in range(hyperparameters["num_hidden_layers"]):
        x = layers.Dense(
            hyperparameters["dense_units"],
            activation=tf.nn.relu)(x)
        x = layers.Dropout(hyperparameters["dropout_rate"])(x)

    outputs = layers.Dense(1, activation=tf.nn.sigmoid)(x)

    model = tf.keras.Model(inputs=inputs, outputs=outputs)

    model.compile(
        optimizer=tf.keras.optimizers.Adam(
            learning_rate=hyperparameters["learning_rate"]),
        loss=tf.keras.losses.BinaryCrossentropy(),
        metrics=[
            tf.keras.metrics.BinaryAccuracy()],
    )

    model.summary()

    return model


def _get_serve_tf_examples_fn(model, tf_transform_output):
    model.tft_layer = tf_transform_output.transform_features_layer()

    @tf.function
    def serve_tf_examples_fn(serialized_tf_examples):
        feature_spec = tf_transform_output.raw_feature_spec()

        feature_spec.pop(LABEL_KEY)

        parsed_features = tf.io.parse_example(serialized_tf_examples, feature_spec)

        transformed_features = model.tft_layer(parsed_features)

        return model(transformed_features)

    return serve_tf_examples_fn


def run_fn(fn_args: FnArgs) -> None:
    hyperparameters = fn_args.hyperparameters["values"]

    log_dir = os.path.join(os.path.dirname(fn_args.serving_model_dir), "logs")

    tensorboard_callback = tf.keras.callbacks.TensorBoard(
        log_dir=log_dir, update_freq="batch"
    )

    model_checkpoint_callback = tf.keras.callbacks.ModelCheckpoint(
        fn_args.serving_model_dir,
        monitor="val_binary_accuracy",
        mode="max",
        verbose=1,
        save_best_only=True,
    )

    callbacks = [
        tensorboard_callback,
        early_stopping_callback,
        model_checkpoint_callback
    ]

    tf_transform_output = tft.TFTransformOutput(fn_args.transform_graph_path)

    train_set = input_fn(
        fn_args.train_files,
        tf_transform_output,
        NUM_EPOCHS)

    eval_set = input_fn(
        fn_args.eval_files,
        tf_transform_output,
        NUM_EPOCHS)

    vectorizer_dataset = train_set.map(
        lambda f, l: f[transformed_name(FEATURE_KEY)]
    )

    vectorizer_layer = layers.TextVectorization(
        max_tokens=5000,
        output_mode="int",
        output_sequence_length=500,
    )

    vectorizer_layer.adapt(vectorizer_dataset)

    model = model_builder(vectorizer_layer, hyperparameters)

    model.fit(
        x=train_set,
        steps_per_epoch=fn_args.train_steps,
        validation_data=eval_set,
        validation_steps=fn_args.eval_steps,
        callbacks=callbacks,
        epochs=NUM_EPOCHS,
        verbose=1,
    )

    signatures = {
        "serving_default": _get_serve_tf_examples_fn(
            model, tf_transform_output
        ).get_concrete_function(
            tf.TensorSpec(
                shape=[None],
                dtype=tf.string,
                name="examples",
            )
        )
    }

    model.save(
        fn_args.serving_model_dir,
        save_format="tf",
        signatures=signatures
    )

Writing trainer.py


In [56]:
from tfx.proto import trainer_pb2

trainer = Trainer(
    module_file=os.path.abspath(TRAINER_MODULE_FILE),
    examples=transform.outputs['transformed_examples'],
    transform_graph=transform.outputs['transform_graph'],
    schema=schema_gen.outputs['schema'],
    hyperparameters=tuner.outputs["best_hyperparameters"],
    train_args=trainer_pb2.TrainArgs(splits=['train']),
    eval_args=trainer_pb2.EvalArgs(splits=['test'])
)

In [57]:
interactive_context.run(trainer)

Model: "model_1"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 clean_text_xf (InputLayer)  [(None, 1)]               0         
                                                                 
 text_vectorization (TextVe  (None, 500)               0         
 ctorization)                                                    
                                                                 
 embedding_1 (Embedding)     (None, 500, 112)          560000    
                                                                 
 bidirectional_1 (Bidirecti  (None, 64)                37120     
 onal)                                                           
                                                                 
 dense_3 (Dense)             (None, 192)               12480     
                                                                 
 dropout_2 (Dropout)         (None, 192)               0   

ExecutionResult(
    component_id: Trainer
    execution_id: 9
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=Trainer, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_run: OutputChannel(artifact_type=ModelRun, producer_component_id=Trainer, output_key=model_run, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

**Layer Details:** Menyediakan ringkasan arsitektur model yang dibangun, termasuk jenis layer, bentuk output, dan jumlah parameter yang digunakan.

**Total Parameters:** Model memiliki total 609,793 parameter, semuanya dapat dilatih.
Epoch Information: Output menunjukkan proses pelatihan selama tiga epoch, termasuk nilai loss dan akurasi biner pada setiap epoch.

- Epoch 1: Loss 0.0525 dan akurasi 98.37% untuk data latih; akurasi validasi 98.32%.
- Epoch 2: Loss menurun menjadi 0.0090 dengan akurasi 99.74% untuk data latih; akurasi validasi meningkat menjadi 98.37%.
- Epoch 3: Loss 0.0072 dan akurasi 99.79% untuk data latih; akurasi validasi meningkat menjadi 98.40%.


Secara keseluruhan, output ini menunjukkan kemajuan pelatihan model yang efektif dengan peningkatan akurasi yang baik pada data validasi.

# Analisis dan Evaluasi Model

In [58]:
from tfx.dsl.components.common.resolver import Resolver
from tfx.dsl.input_resolution.strategies.latest_blessed_model_strategy import LatestBlessedModelStrategy
from tfx.types import Channel
from tfx.types.standard_artifacts import Model, ModelBlessing

model_resolver = Resolver(
    strategy_class=LatestBlessedModelStrategy,
    model=Channel(type=Model),
    model_blessing=Channel(type=ModelBlessing)
).with_id("latest_blessed_model_resolver")

In [59]:
interactive_context.run(model_resolver)

ExecutionResult(
    component_id: latest_blessed_model_resolver
    execution_id: 10
    outputs:
        model: OutputChannel(artifact_type=Model, producer_component_id=latest_blessed_model_resolver, output_key=model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        model_blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=latest_blessed_model_resolver, output_key=model_blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [68]:
import tensorflow_model_analysis as tfma

eval_config = tfma.EvalConfig(
    model_specs=[tfma.ModelSpec(label_key='fraudulent')],
    slicing_specs=[tfma.SlicingSpec()],
    metrics_specs=[
        tfma.MetricsSpec(metrics=[
            tfma.MetricConfig(class_name='ExampleCount'),
            tfma.MetricConfig(class_name='AUC'),
            tfma.MetricConfig(class_name='FalsePositives'),
            tfma.MetricConfig(class_name='TruePositives'),
            tfma.MetricConfig(class_name='FalseNegatives'),
            tfma.MetricConfig(class_name='TrueNegatives'),
            tfma.MetricConfig(class_name='BinaryAccuracy',
                              threshold=tfma.MetricThreshold(
                                  value_threshold=tfma.GenericValueThreshold(
                                      lower_bound={'value': 0.5}),
                                  change_threshold=tfma.GenericChangeThreshold(
                                      direction=tfma.MetricDirection.HIGHER_IS_BETTER,
                                      absolute={'value': 0.0001})
                              )
            )
        ])
    ]
)

In [72]:
from tfx.components import Evaluator

model_analyzer = Evaluator(
    examples=example_gen.outputs["examples"],
    model=trainer.outputs["model"],
    baseline_model=model_resolver.outputs["model"],
    eval_config=eval_config,
    example_splits=['test']
)

In [73]:
interactive_context.run(model_analyzer)

Instructions for updating:
Use eager execution and: 
`tf.data.TFRecordDataset(path)`


ExecutionResult(
    component_id: Evaluator
    execution_id: 14
    outputs:
        evaluation: OutputChannel(artifact_type=ModelEvaluation, producer_component_id=Evaluator, output_key=evaluation, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False)
        blessing: OutputChannel(artifact_type=ModelBlessing, producer_component_id=Evaluator, output_key=blessing, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

memuat dan menampilkan hasil evaluasi model yang telah dilakukan menggunakan TensorFlow Model Analysis (TFMA).

In [74]:
eval_result = model_analyzer.outputs['evaluation'].get()[0].uri
tfma_result = tfma.load_eval_result(eval_result)
tfma.view.render_slicing_metrics(tfma_result)
tfma.addons.fairness.view.widget_view.render_fairness_indicator(tfma_result)

In [75]:
from tfx.components import Pusher
from tfx.proto import pusher_pb2

pusher = Pusher(
    model=trainer.outputs["model"],
    model_blessing=model_analyzer.outputs["blessing"],
    push_destination=pusher_pb2.PushDestination(
        filesystem=pusher_pb2.PushDestination.Filesystem(
            base_directory='serving_model_dir/real-or-fake-jobs-detection-model'
        )
    )
)

In [76]:
interactive_context.run(pusher)

ExecutionResult(
    component_id: Pusher
    execution_id: 15
    outputs:
        pushed_model: OutputChannel(artifact_type=PushedModel, producer_component_id=Pusher, output_key=pushed_model, additional_properties={}, additional_custom_properties={}, _input_trigger=None, _is_async=False))

In [77]:

!pip freeze > requirements.txt